#LREC 2022
##Hyperparameter Tuning

# Data Extraction

In [ ]:
#Installing libraries
!pip install simpletransformers
!pip install wandb --upgrade

In [1]:
#Importing libraries
import os
import json
import pprint
import pandas as pd
import numpy as np
import math
from sklearn.metrics import (hamming_loss, 
                             label_ranking_average_precision_score,
                             f1_score,
                             accuracy_score,
                             multilabel_confusion_matrix)
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
import wandb
import torch
import logging

# Data Pre-Processing

In [ ]:
#Creating Python Object from Dataset
with open('rationales_forced_labour_dataset.json', 'r') as json_file: #Data set path
  dataset = json.load(json_file)

#Creating DataFrame
dataset_df = pd.DataFrame(dataset)
print('Dataset:', dataset_df.shape)

#Creating Training, Validation and Test Set
train_df = dataset_df.loc[dataset_df['set']=='train', ['content', 'labels']]
val_df = dataset_df.loc[dataset_df['set']=='dev', ['content', 'labels']]
test_df = dataset_df.loc[dataset_df['set']=='test', ['content', 'labels']]

print('Training Set:', train_df.shape)
print('Validation Set:', val_df.shape)
print('Test Set:', test_df.shape)

Dataset: (646, 2)
Training Set: (452, 2)
Validation Set: (65, 2)
Test Set: (129, 2)


# Defining the Sweep

In [24]:
#Defining a method
sweep_config = {
    'method': 'random'
}

In [25]:
#Defining metrics
metric = {
    'name': 'val_loss',
    'goal': 'minimize'
}

sweep_config['metric'] = metric

In [26]:
#Defining Hyperparameters Range
parameters_dict = {
    'learning_rate': {
        'distribution': 'log_uniform',
        'min': math.log(0.00001),
        'max': math.log(0.01)
    },
    'optimizer': {
        'values': ['AdamW','Adafactor']
    },
    'train_batch_size': {
        'values': [2, 4, 6, 8]
    },
    'threshold': {
        'values': [0.15, 0.20, 0.25, 0.30, 0.35, 0.40]
    },
}
sweep_config['parameters'] = parameters_dict

In [27]:
#Checking sweep configuration
pprint.pprint(sweep_config)

{'method': 'random',
 'metric': {'goal': 'minimize', 'name': 'val_loss'},
 'parameters': {'learning_rate': {'distribution': 'log_uniform',
                                  'max': -4.605170185988091,
                                  'min': -11.512925464970229},
                'optimizer': {'values': ['AdamW', 'Adafactor']},
                'threshold': {'values': [0.15, 0.2, 0.25, 0.3, 0.35, 0.4]},
                'train_batch_size': {'values': [2, 4, 6, 8]}}}


# W&B Setup

In [28]:
#Logging W&B
wandb.login()

<IPython.core.display.Javascript object>

wandb: You can find your API key in your browser here: https://wandb.ai/authorize


wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

# Initialising the sweep

In [29]:
#Initialising sweep (Include Project Name)
project_name = 'hp_tuning_date_model' #wandb_project_name
sweep_id = wandb.sweep(sweep_config, project = project_name)

Create sweep with ID: d43dafg0
Sweep URL: https://wandb.ai/erickmendezg/hp_tuning_date_model/sweeps/d43dafg0


# Model Training

In [30]:
#SimpleTransformers setup
logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

In [31]:
#Model arguments
model_args = MultiLabelClassificationArgs()
model_args.reprocess_input_data = True
model_args.overwrite_output_dir = True
model_args.num_train_epochs = 3
model_args.wandb_project = project_name
model_args.overwrite_output_dir = True
model_args.evaluate_during_training = True
model_args.adafactor_relative_step = False
model_args.adafactor_warmup_init = False

In [32]:
#Training function
def train():
  
  #Initialising a new wandb run
  wandb.init()  

  #Creating Model
  model = MultiLabelClassificationModel(
      "roberta", #model_type
      "roberta-base", #model_name
      num_labels=11,
      use_cuda=torch.cuda.is_available(),
      args=model_args,
      sweep_config = wandb.config
      )
  
  #Training the model
  model.train_model(train_df, eval_df = val_df)

  #Evaluate the model
  model.eval_model(val_df)

  #Sync wandb
  wandb.join()

# Run the Sweep agent

In [33]:
#Run the sweep agent
wandb.agent(sweep_id, train, count=40)

INFO:wandb.agents.pyagent:Starting sweep agent: entity=None, project=None, count=40
wandb: Agent Starting Run: obi914k0 with config:
wandb: 	learning_rate: 0.0004058963042185313
wandb: 	optimizer: Adafactor
wandb: 	threshold: 0.15
wandb: 	train_batch_size: 6
wandb: Currently logged in as: erickmendezg (use `wandb login --relogin` to force relogin)


Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/478M [00:00<?, ?B/s]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForMultiLabelSequenceClassification: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaForMultiLabelSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForMultiLabelSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.out_proj.weight', 'c

Downloading:   0%|          | 0.00/878k [00:00<?, ?B/s]

...

  0%|          | 0/103 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_utils: Saving features into cached file cache_dir/cached_dev_roberta_128_0_2
INFO:simpletransformers.classification.classification_model: Training of roberta model complete. Saved to outputs/.
/usr/local/lib/python3.7/dist-packages/simpletransformers/classification/classification_model.py:1427: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  "Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels."
INFO:simpletransformers.classification.classification_utils: Converting to features started. Cache is not used.


  0%|          | 0/103 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_utils: Saving features into cached file cache_dir/cached_dev_roberta_128_0_2


Running Evaluation:   0%|          | 0/13 [00:00<?, ?it/s]